# **Homework2**
### Group 1: Swathi Rai, Faraz Ahmad, Jorge Palacio

In [5]:
'''
!pip install llama-index-readers-file
!pip install llama-index-llms-openai
!pip install llama-index-embeddings-openai
!pip install llama-index-vector-stores-pinecone
!pip install llama-index-readers-file
!pip install llama-index-vector-stores-postgres
!pip install llama-index-embeddings-huggingface
!pip install llama-index-vector-stores-pinecone
!pip -q install python-dotenv pinecone-client llama-index pymupdf
!pip3 install pinecone-client
!pip3 install "pinecone-client[grpc]"
!pip install wget
!pip install faiss-cpu
!pip install langchain_community
!pip install pypdf
!pip install sentence_transformers
!pip install langchain_experimental
!pip install transformers
!pip install -c pytorch faiss-cpu #conda
!pip install langchain_openai 

!pip install langchain-community langchain-core
!pip install langchain langchain_openai
!pip install langchain_experimental
'''

'\n!pip install llama-index-readers-file\n!pip install llama-index-llms-openai\n!pip install llama-index-embeddings-openai\n!pip install llama-index-vector-stores-pinecone\n!pip install llama-index-readers-file\n!pip install llama-index-vector-stores-postgres\n!pip install llama-index-embeddings-huggingface\n!pip install llama-index-vector-stores-pinecone\n!pip -q install python-dotenv pinecone-client llama-index pymupdf\n!pip3 install pinecone-client\n!pip3 install "pinecone-client[grpc]"\n!pip install wget\n!pip install faiss-cpu\n!pip install langchain_community\n!pip install pypdf\n!pip install sentence_transformers\n!pip install langchain_experimental\n!pip install transformers\n!pip install -c pytorch faiss-cpu #conda\n!pip install langchain_openai \n\n!pip install langchain-community langchain-core\n!pip install langchain langchain_openai\n!pip install langchain_experimental\n'

In [1]:
import os, io, json, transformers, pinecone, fitz, pypdf, faiss, sqlite3, langchain_community, langchain, openai, math, time 
from transformers import pipeline
import pandas as pd
import numpy as np
from io import StringIO
from dotenv import load_dotenv
from operator import itemgetter

from langchain import document_loaders, embeddings
from langchain.vectorstores import FAISS
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_experimental.text_splitter import SemanticChunker
from langchain_community.vectorstores import FAISS
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnableLambda, RunnablePassthrough
from langchain_openai import ChatOpenAI, OpenAIEmbeddings

from pinecone import Pinecone, ServerlessSpec, Pinecone         # vector store

from llama_index.core import (
    VectorStoreIndex,
    StorageContext,
    SimpleDirectoryReader
)
from llama_index.core.node_parser import SentenceSplitter
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.core.node_parser import SentenceSplitter
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.vector_stores.pinecone import PineconeVectorStore
from llama_index.core.schema import TextNode
from llama_index.core.extractors import (
    QuestionsAnsweredExtractor,
    TitleExtractor,
)
from llama_index.core.ingestion import IngestionPipeline
from llama_index.llms.openai import OpenAI

from sentence_transformers import SentenceTransformer

# sentence transformers
from llama_index.embeddings.huggingface import HuggingFaceEmbedding


In [2]:
load_dotenv()

#Anyscale Endpoint API Key:
## https://www.anyscale.com/endpoints
access_endpoint_api_key =os.getenv('access_endpoint_api_key') # this is for the bonus questions/not needed otherwise

# OpenAI API Key:
openai = os.getenv('OPENAI_API_KEY')

# Pinecone API Key:
pinecone_api_key =os.getenv('PINECONE_API_KEY')
environment =os.getenv('PINECONE_ENV')

HF_TOKEN = os.getenv('HF_TOKEN')

# configure Pinecone client
pc = Pinecone(api_key=pinecone_api_key)

# **Homework**

### **Create a Pinecone Index**

In [3]:
use_serverless = os.environ.get("USE_SERVERLESS", "False").lower() == "true"

In [9]:
if use_serverless:
    spec = pinecone.ServerlessSpec(cloud='aws', region='us-west-2')
else:
    spec = pinecone.PodSpec(environment=environment)

In [10]:
# Name our Pinecone Index:
index_name = "hw02"

In [11]:
# Name our Pinecone Index:
index_name = "hw02"

# If a Pinecone index of the same name already exists, delete it:
if index_name in pc.list_indexes().names():
    pc.delete_index(index_name)

In [12]:
# define parameters for and create the index:

dimensions = 1536              # the dimensions of the index need to align with the LLM we are using for the RAG system. For example, if using openAI then dimenion = 1536. If using Llama2, then dimension = 384.

pc.create_index(
    name=index_name, 
    dimension=dimensions, 
    metric="cosine",          # we can use different distance metrics to measure the similarity between vector embeddings and user queries. this is where we define what similarity metric we are going to use for the vector store.
    spec=spec
)

# wait for index to be ready before connecting
while not pc.describe_index(index_name).status['ready']:
    time.sleep(1)

In [13]:
for index in pc.list_indexes():
    print(index['name'])

hw02


In [14]:
pc.describe_index("hw02")

{'dimension': 1536,
 'host': 'hw02-cmx69u7.svc.gcp-starter.pinecone.io',
 'metric': 'cosine',
 'name': 'hw02',
 'spec': {'pod': {'environment': 'gcp-starter',
                  'pod_type': 'starter',
                  'pods': 1,
                  'replicas': 1,
                  'shards': 1}},
 'status': {'ready': True, 'state': 'Ready'}}

In [15]:
index = pc.Index(index_name)  # create an index to use in the vector store

In [16]:
index_stats_response = index.describe_index_stats()
index_stats_response 

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [17]:
vector_store = PineconeVectorStore(pinecone_index=index)    # this function creates a vector store where we will add and store embeddings

# **Homework 2 Assignment**

## **Section A. Experimenting with Vector Store Query Design (50 points)**

In [19]:
import json, os, io, re, requests, fitz
import requests
from langchain_text_splitters import RecursiveJsonSplitter
from langchain_experimental.text_splitter import SemanticChunker
from langchain_openai.embeddings import OpenAIEmbeddings

from llama_index.core import (
    VectorStoreIndex,
    StorageContext,
    SimpleDirectoryReader
)
from llama_index.core.node_parser import SentenceSplitter
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.vector_stores.pinecone import PineconeVectorStore
from llama_index.core.schema import TextNode
from llama_index.core.extractors import (
    QuestionsAnsweredExtractor,
    TitleExtractor,
)
from llama_index.core.ingestion import IngestionPipeline
from llama_index.llms.openai import OpenAI

# sentence transformers
from llama_index.embeddings.huggingface import HuggingFaceEmbedding

In [5]:
load_dotenv()

access_endpoint_api_key =os.getenv('access_endpoint_api_key')
openai = os.getenv('OPENAI_API_KEY')
pinecone_api_key =os.getenv('PINECONE_API_KEY')
environment =os.getenv('PINECONE_ENV')
HF_TOKEN = os.getenv('HF_TOKEN')

# configure Pinecone client
pc = Pinecone(api_key=pinecone_api_key)

In [4]:
doc = fitz.open("data/the-word-2023-24-12.11.23.pdf")

### **Choose a method to chunk the text data:**

- [Semantic chunking](https://python.langchain.com/docs/modules/data_connection/document_transformers/semantic-chunker)

- [Recursive chunking](https://python.langchain.com/docs/modules/data_connection/document_transformers/recursive_text_splitter)

- [Character chunking](https://python.langchain.com/docs/modules/data_connection/document_transformers/character_text_splitter)

- [Token chunking](https://python.langchain.com/docs/modules/data_connection/document_transformers/split_by_token)

##### Choose a type of chunker (From langchain):

In [45]:
from langchain_experimental.text_splitter import SemanticChunker

# parser to split up PDF:
text_parser = SentenceSplitter(
    chunk_size=1024
)

In [46]:
text_chunks = []
doc_idxs = []


for doc_idx, page in enumerate(doc):
    page_text = page.get_text("text")
    cur_text_chunks = text_parser.split_text(page_text)
    text_chunks.extend(cur_text_chunks)
    doc_idxs.extend([doc_idx] * len(cur_text_chunks))

In [47]:
text_chunks

['1 \n \n \n \nThe Word: Student Handbook \n2023-2024',
 '2 \n \n \nWelcome to The Word 2023-2024 \n \nThe Word student handbook contains information and resources to help you create your \nCarnegie Mellon experience and embrace your role as a valued member of our university. \n \nAt Carnegie Mellon, our ambition is that all students will reach their highest potential in the \nareas of intellectual and artistic pursuits, personal well-being, professional development, \nleadership, and contribution to the larger community. \n \nCommunity membership affords many privileges and likewise responsibilities as we all uphold \nthe standards of our university. To ensure you are knowledgeable of the university’s \nexpectations and the process that will be followed if standards are not met, this handbook \narticulates the rights and responsibilities afforded to and expected of each member of our \ncommunity. \n \nWe hope you will take advantage of this handbook as you prepare for your successful 

In [48]:
nodes = []

for idx, text_chunk in enumerate(text_chunks):
    node = TextNode(
        text=text_chunk,
    )
    src_doc_idx = doc_idxs[idx]
    src_page = doc[src_doc_idx]
    nodes.append(node)
nodes

[TextNode(id_='91061e28-d348-405f-8bee-5100a5c5de19', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, text='1 \n \n \n \nThe Word: Student Handbook \n2023-2024', start_char_idx=None, end_char_idx=None, text_template='{metadata_str}\n\n{content}', metadata_template='{key}: {value}', metadata_seperator='\n'),
 TextNode(id_='cf4355e5-59b0-42fb-912f-0b2d2fcd9be1', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, text='2 \n \n \nWelcome to The Word 2023-2024 \n \nThe Word student handbook contains information and resources to help you create your \nCarnegie Mellon experience and embrace your role as a valued member of our university. \n \nAt Carnegie Mellon, our ambition is that all students will reach their highest potential in the \nareas of intellectual and artistic pursuits, personal well-being, professional development, \nleadership, and contribution to the large

#### **Chunker Choices**

In [ ]:
# Chunker choice #1: Sentence Chunking

### **Create the vector store using chosen similarity metrics:**

In [49]:
use_serverless = os.environ.get("USE_SERVERLESS", "False").lower() == "true"

if use_serverless:
    spec = pinecone.ServerlessSpec(cloud='aws', region='us-west-2')
else:
    spec = pinecone.PodSpec(environment=environment)

# Name our Pinecone Index:
index_name = "hw02"

# If a Pinecone index of the same name already exists, delete it:
if index_name in pc.list_indexes().names():
    pc.delete_index(index_name)

### **choose a similarity metric to use for the vector store:**

In [50]:
# Name our Pinecone Index:
index_name = "hw02"

# define similarity and additional parameters for the vector store index:

dimensions = 1536 #768              # the dimensions of the index need to align with the LLM we are using for the RAG system. For example, if using openAI then dimenion = 1536. If using Llama2, then dimension = 384.

# "dotproduct" is one similarity metric we can for the vector store index. We can use different distance metrics to measure the similarity between vector embeddings and user queries. This is where we define what similarity metric we are going to use for the vector store.
# "cosine" is another similarity metric we can use for the vector store index.
# "euclidean" is another similarity metric we can use for the vector store index.

pc.create_index(
    name=index_name, 
    dimension=dimensions, 
    metric="cosine",          # we can use different distance metrics to measure the similarity between vector embeddings and user queries. this is where we define what similarity metric we are going to use for the vector store.
    spec=spec
)

# wait for index to be ready before connecting
while not pc.describe_index(index_name).status['ready']:
    time.sleep(1)

for index in pc.list_indexes():
    print(index['name'])


pc.describe_index("hw02")


pc_index = pc.Index(index_name)  # create an index to use in the vector store


vector_store = PineconeVectorStore(pinecone_index=pc_index)    # this function creates a vector store where we will add and store embeddings

hw02


In [51]:

pc_index.describe_index_stats()


{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [52]:
llm = OpenAI(model="gpt-3.5-turbo")

extractors = [
    TitleExtractor(nodes=5, llm=llm),
    QuestionsAnsweredExtractor(questions=3, llm=llm),
]

pipeline = IngestionPipeline(
    transformations=extractors,
)
nodes = await pipeline.arun(nodes=nodes, in_place=False)

  0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 297/297 [02:02<00:00,  2.43it/s]


### ***choose an embedding model to use for the vector store:**

#### **OpenAI Embeddings**

In [53]:
model_ada="text-embedding-ada-002"
small_txt_embedmodel_="text-embedding-3-small"


In [54]:
embed_model = OpenAIEmbedding(model="text-embedding-3-small", openai_api_key=openai)

for node in nodes:
    node_embedding = embed_model.get_text_embedding(
        node.get_content(metadata_mode="all")
    )
    node.embedding = node_embedding

### **load the embeddings into the vector store (e.g. create a vector store):**

In [55]:
vector_store.add(nodes)

Upserted vectors:   0%|          | 0/297 [00:00<?, ?it/s]

['91061e28-d348-405f-8bee-5100a5c5de19',
 'cf4355e5-59b0-42fb-912f-0b2d2fcd9be1',
 '17ded2bf-b99c-4ff7-9a4d-b4a9339c03de',
 'c9b6a070-1b74-4282-94ed-81074cd0e054',
 '06eb62a3-81f3-4cfa-837c-7cb6f86e4a20',
 '7daebd80-2af4-42a3-a7a2-173030f49e03',
 '486cc8ca-079b-4b8d-b0d5-31adfb4ea908',
 '1d7782f1-be5e-498f-83cd-1f9395d3f6cf',
 '82ee3e46-5fb9-4fa4-b13c-1daee19bf7d2',
 '29c15916-0478-4be9-a552-a087542217f0',
 '9968d8f4-0359-4ded-91a4-23f39d58d880',
 '912a4c04-6092-4947-ab91-20853bfd0230',
 'ff66ea30-5d42-48de-98b7-36fa2729e302',
 '89d7acc7-9269-4246-be26-f81d77bc5de8',
 '2c983ae2-b68a-48c4-abd1-e06dfa862e11',
 '68cb67b1-40e7-4ac4-a6ca-ca7ca253e78b',
 'a1e2d969-9afd-4cd7-ac2c-77ee8853e577',
 'cebf10b7-9e9a-40da-8b3c-5f543df7b892',
 'eaf8905d-2229-47ea-b09b-a4aec333727c',
 '8c8e86a8-d2a1-4855-bfd7-8424c26704a5',
 '4241b440-16ed-4162-b33a-de225991e01f',
 '9ce9820e-1e27-43c8-a3e0-5cc071fd0581',
 'bc2899d2-7ba5-479e-8a3e-7b784441007d',
 '144dd75d-6043-4365-a7cc-ddda77cc044a',
 '18dbee14-9a9b-

In [57]:

pc_index.describe_index_stats()


{'dimension': 1536,
 'index_fullness': 0.00297,
 'namespaces': {'': {'vector_count': 297}},
 'total_vector_count': 297}

In [30]:
print(nodes[0].metadata)

{'document_title': 'Carnegie Mellon University Student Handbook: Academic Policies, Community Resources, and Code of Conduct', 'questions_this_excerpt_can_answer': '1. What are the specific rights and responsibilities afforded to each member of the Carnegie Mellon University community according to the Student Handbook?\n2. Who are the key individuals responsible for overseeing education, student affairs, and the code of conduct at Carnegie Mellon University?\n3. What is the overarching vision and mission of Carnegie Mellon University as outlined in the Student Handbook?'}


In [31]:
print(nodes[0])

Node ID: e8017f28-b912-4a46-a231-2a1017ca87ff
Text: 0       1       The Word: Student Handbook  2023-2024  2
Welcome to The Word 2023-2024    The Word student handbook contains
information and resources to help you create your  Carnegie Mellon
experience and embrace your role as a valued member of our university.
At Carnegie Mellon, our ambition is that all students will reach their
highest ...


In [32]:
nodes[1]

TextNode(id_='4ed7a145-27ba-4c49-8efa-0770dc12d775', embedding=[-0.019559256732463837, -0.007248909678310156, 0.0152541259303689, 0.049008678644895554, -0.018267717212438583, 0.03174161538481712, -0.005256331991404295, -0.03262590989470482, 0.000663586484733969, 0.025411907583475113, 0.041422341018915176, -0.038560010492801666, 0.009087316691875458, 0.016906365752220154, -0.0029074177145957947, 0.02773900516331196, -0.020955516025424004, 0.038048047572374344, 0.0028681480325758457, 0.053197454661130905, 0.028390591964125633, 0.061063043773174286, -0.0088953310623765, 0.03753608837723732, -0.0025918050669133663, -0.031881239265203476, 0.024760320782661438, 0.008267015218734741, 0.00171332573518157, 0.01495160348713398, 0.003444104688242078, -0.022375045344233513, -0.02466723695397377, -0.036512162536382675, -0.026621999219059944, 0.02680816687643528, -0.02090897411108017, -0.010431216098368168, -0.011298059485852718, 0.00171332573518157, -0.06194734200835228, -0.02643583156168461, -0.01

### **Retrieve Content from the Vector Store**

In [ ]:
from openai import OpenAI
client = OpenAI()

In [ ]:
query = (
    "animal pet fish policy"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
res2 = pc_index.query(vector=xq, top_k=2, include_metadata=False)

In [ ]:
res2

{'matches': [{'id': 'ac203fcb-19ec-4ff0-a769-1059b3186852',
              'score': 0.0818191916,
              'values': []},
             {'id': '3d0c3687-65fe-4a5f-b5a3-a5567ae7e58a',
              'score': 0.0701709315,
              'values': []}],
 'namespace': '',
 'usage': {'read_units': 5}}

In [ ]:
for index, result in enumerate(res2.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')

Result  0 (score= 0.0818191916 )  Node ID: ac203fcb-19ec-4ff0-a769-1059b3186852
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0701709315 )  Node ID: 3d0c3687-65fe-4a5f-b5a3-a5567ae7e58a
Text: 149      • Counseling & Psychological Services — Counseling and
Psychological Services (CaPS) is  available as a resource to students
for initial assessment of drug and alcohol use, and  referrals to off
campus outpatient and inpatient treatment programs.  • University
Health Services — University Health Services (UHS) also provides
students  wi... 
----------


#### **Query the vector store using these queries**

**Instruction: set the 'k' parameter to 5**

Query 1: What is the policy statement for the academic integrity policy?


Query 2: What is the policy violation definition for cheating?

Query 3: What is the policy statement for improper or illegal communications?

Query 4: What are CMU’s quiet hours?

Query 5: Where are pets allowed on CMU?


### ***Query the vector store with the 5 queries above (don't forget to record the responses in your homework submission!):***

In [ ]:
# query the vector store with the 5 queries above (don't forget to record the responses in your homework submission!):

In [ ]:
query = (
    "What is the policy statement for the academic integrity policy?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=5, include_metadata=False)
print("Query: ", query)
for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index+1,'(score=',result.score,') ',node,'\n----------')
            print("Expanded Version\n")
            print('Text:', node.text)
            print('----------')


Query:  What is the policy statement for the academic integrity policy?
Result  1 (score= 0.0815214068 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Expanded Version

Text: 51 
 
 
study (five for architecture) based upon the maintenance of a specific cumulative quality 
point average. The academic scholarship renewal criteria are included in the scholarship 
notification letter which is mailed to the student prior to the May 1 matriculation deadline. 
Each scholarship recipient's cumulative quality point average is reviewed at the end of 
each academic year. If the student achieves the scholarship renewal criteria, then 

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)
print('Query:' ,query)
embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=5, include_metadata=False)
for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index+1,'(score=',result.score,') ',node,'\n----------')
            print("Expanded Version\n")
            print('Text:', node.text)
            print('----------')

Query: What is the policy violation definition for cheating?
Result  1 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Expanded Version

Text: 51 
 
 
study (five for architecture) based upon the maintenance of a specific cumulative quality 
point average. The academic scholarship renewal criteria are included in the scholarship 
notification letter which is mailed to the student prior to the May 1 matriculation deadline. 
Each scholarship recipient's cumulative quality point average is reviewed at the end of 
each academic year. If the student achieves the scholarship renewal criteria, then the 
schola

In [ ]:
query = (
    "What is the policy statement for improper or illegal communications?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=5, include_metadata=False)
print("Query: ", query)
for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index+1,'(score=',result.score,') ',node,'\n----------')
            print("Expanded Version\n")
            print('Text:', node.text)
            print('----------')

Query:  What is the policy statement for improper or illegal communications?
Result  1 (score= 0.0833253935 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Expanded Version

Text: 51 
 
 
study (five for architecture) based upon the maintenance of a specific cumulative quality 
point average. The academic scholarship renewal criteria are included in the scholarship 
notification letter which is mailed to the student prior to the May 1 matriculation deadline. 
Each scholarship recipient's cumulative quality point average is reviewed at the end of 
each academic year. If the student achieves the scholarship renewal criteria, 

In [ ]:
query = (
    "What are CMU’s quiet hours?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=5, include_metadata=False)
print("Query:", query)
for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index+1,'(score=',result.score,') ',node,'\n----------')
            print("Expanded Version\n")
            print('Text:', node.text)
            print('----------')

Query: What are CMU’s quiet hours?
Result  1 (score= 0.0651899725 )  Node ID: ac21b935-4255-459a-9a0f-f648c3c4eec8
Text: 18      6.  Falsification of academic credentials.  Plagiarism
is defined as the use of work or concepts contributed by other
individuals  without proper attribution or citation. Unique ideas or
materials taken from another  source for either written or oral use
must be fully acknowledged in academic work to be  graded. Examples of
sources expec... 
----------
Expanded Version

Text: 18 
 
 
6. 
Falsification of academic credentials. 
Plagiarism is defined as the use of work or concepts contributed by other individuals 
without proper attribution or citation. Unique ideas or materials taken from another 
source for either written or oral use must be fully acknowledged in academic work to be 
graded. Examples of sources expected to be referenced include but are not limited to: 
1. 
Text, either written or spoken, quoted directly or paraphrased. 
2. 
Graphic elements. 

In [ ]:
query = (
    "Where are pets allowed on CMU?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=5, include_metadata=False)
print("Query: ", query)
for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index+1,'(score=',result.score,') ',node,'\n----------')
            print("Expanded Version\n")
            print('Text:', node.text)
            print('----------')
            

Query:  Where are pets allowed on CMU?
Result  1 (score= 0.0808195919 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Expanded Version

Text: 51 
 
 
study (five for architecture) based upon the maintenance of a specific cumulative quality 
point average. The academic scholarship renewal criteria are included in the scholarship 
notification letter which is mailed to the student prior to the May 1 matriculation deadline. 
Each scholarship recipient's cumulative quality point average is reviewed at the end of 
each academic year. If the student achieves the scholarship renewal criteria, then the 
scholarship is automatically

### **Homework Questions:**

**A.II.** Explain your rationale for choosing the similarity metric you decided to use in the vector store. What is one pro of using the metric, and what is one difference between using the metric you selected and the other two similarity metrics we discussed in the lab. (We discussed cosine, dot product, and euclidean similarity metrics). 







**A.III.** Copy and paste the results or information retrieved from the vector store in response to each of the queries you submitted to the vector store.  

	Response 1 (to Query 1): 



	Response 2 (to Query 2): 


	Response 3 (to Query 3): 


	Response 4 (to Query 4): 


	Response 5 (to Query 5): 
	

**A.IV.** Qualitatively analyze the responses to your queries submitted to the vector store. Did the queries retrieve the information you were expecting to obtain. Why or why not? Why do you think the queries were successful / unsuccessful in retrieving the information you expected or needed? 

## **Section B. Experimenting with Vector Store Embeddings & Query Parameters (50 points)**

1) Choose 1 of the 5 queries provided in A.1.6.A, above, and experiment with submitting the query to the vector store by changing the search parameters in the following manner:


*   A) Baseline query, e.g. query, k=5.

*   B) Query, parameter k = 10

*   C) Query, parameter k = 50

*   D) Query, parameter k = 75

*   E) Query, parameter k = 100

*   F) Query, parameter k = 500

**In your written homework submission, record the responses/results of each query submitted to the vector store.**


In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=1000, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')





Result  0 (score= 0.0945086554 )  Node ID: 3cfc6957-e8dc-4529-8dd0-d2a55f1ceb4f
Text: 8       Use of an alternate, stand-in or proxy during an
examination. 3. Copying from the examination or work of another person
or source. 4. Submission or use of falsified data. 5. Using false
statements to obtain additional time or other accommodation. 18
6. 
----------
Result  1 (score= 0.0910882205 )  Node ID: 717c4ef1-51af-4a75-885a-5451a4799d55
Text: 181       The  University Police are responsible for keeping the
tunnels locked and apprehending anyone  who trespasses in them.
Student Accounts Receivable Collection Policy and Procedures  Please
refer to the current Student Financial Obligation Statement. That
statement is  provided to all students through the Student Information
Online (SIO). 
----------
Result  2 (score= 0.0910409093 )  Node ID: a31bda62-5c54-4044-a02a-b1084b1aed54
Text: 115       Participate in periodic safety inspections of the work
area. Environmental Health and Safety Autho

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=10, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')





Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=50, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')





Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=75, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')




Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=100, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')




Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=500, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')




Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

# get relevant contexts (including the questions)
reshw = pc_index.query(vector=xq, top_k=1000, include_metadata=False)

for index, result in enumerate(reshw.matches):
    for node in nodes:
        if node.id_ == result.id:
            print('Result ',index,'(score=',result.score,') ',node,'\n----------')




Result  0 (score= 0.0922130719 )  Node ID: 1dffaf0c-e05b-4f62-9676-778b0a33a202
Text: 51      study (five for architecture) based upon the maintenance
of a specific cumulative quality  point average. The academic
scholarship renewal criteria are included in the scholarship
notification letter which is mailed to the student prior to the May 1
matriculation deadline.  Each scholarship recipient's cumulative
quality point average i... 
----------
Result  1 (score= 0.0893182606 )  Node ID: e8f46e61-2dfd-4185-9abe-b1e34682a1cb
Text: 19        Procedures for dealing with allegations of these
policy violations are detailed in the  university’s Academic
Disciplinary Action Procedures, which are published in The WORD
student handbook. Periodic review of these procedures will be overseen
by the Dean of  Student Affairs or her/his designee in consultation
with Faculty Senate and... 
----------
Result  2 (score= 0.0890862122 )  Node ID: 5a74f618-e651-47b3-970e-0853602e24c2
Text: 31      • Resellin

2. Return to step A.1.B., above, and select a different text chunking method (e.g. word, sentence, paragraph). 
- Chunk your text data using the method. Create embeddings for the text. 
- Load the embeddings into the vector store. 
- Submit the same query you selected in B.1, above, and submit it to the vector store 6 times (using the different ‘k’ parameter settings defined in B.1, above), and record the responses.

**In your written homework submission, record the responses/results of each query submitted to the vector store.**

In [6]:
# Chunker choice #2: Semantic paragraph chunking

from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from langchain_experimental.text_splitter import SemanticChunker
from llama_index.core.node_parser import SemanticSplitterNodeParser
# parser to split up PDF resume:


text_splitter= SemanticChunker(OpenAIEmbeddings())
import json
df_path = "data/the-word-2023-24-12.11.23.json"
f = open(df_path)
data = json.load(f)
data= data['text']
data

'1 \n  \n \nThe Word: Student Handbook \n2023-2024 \n2 \n \n \nWelcome to The Word 2023-2024 \n \nThe Word student handbook contains information and resources to help you create your \nCarnegie Mellon experience and embrace your role as a valued member of our university. \n \nAt Carnegie Mellon, our ambition is that all students will reach their highest potential in the \nareas of intellectual and artistic pursuits, personal well-being, professional development, \nleadership, and contribution to the larger community. \n \nCommunity membership affords many privileges and likewise responsibilities as we all uphold \nthe standards of our university. To ensure you are knowledgeable of the university’s \nexpectations and the process that will be followed if standards are not met, this handbook \narticulates the rights and responsibilities afforded to and expected of each member of our \ncommunity. \n \nWe hope you will take advantage of this handbook as you prepare for your successful Carne

In [7]:
docs_semantic_chunks = text_splitter.split_text(data)


In [8]:

semantic_chunks = []
doc_idxs_semantic = []
for doc_idx, page in enumerate(docs_semantic_chunks):
    semantic_chunks.append(str(doc_idx)+" \n \n \n "+page)
    doc_idxs_semantic.append(doc_idx)  


In [9]:
semantic_chunks


['0 \n \n \n 1 \n  \n \nThe Word: Student Handbook \n2023-2024 \n2 \n \n \nWelcome to The Word 2023-2024 \n \nThe Word student handbook contains information and resources to help you create your \nCarnegie Mellon experience and embrace your role as a valued member of our university. At Carnegie Mellon, our ambition is that all students will reach their highest potential in the \nareas of intellectual and artistic pursuits, personal well-being, professional development, \nleadership, and contribution to the larger community. Community membership affords many privileges and likewise responsibilities as we all uphold \nthe standards of our university. To ensure you are knowledgeable of the university’s \nexpectations and the process that will be followed if standards are not met, this handbook \narticulates the rights and responsibilities afforded to and expected of each member of our \ncommunity. We hope you will take advantage of this handbook as you prepare for your successful Carnegie

In [10]:
len(semantic_chunks)


205

In [11]:
len(doc_idxs_semantic)

205

In [12]:
nodes = []
for idx, text_chunk in enumerate(semantic_chunks):
    node = TextNode(
        text=text_chunk,
    )
    src_doc_idx = doc_idxs_semantic[idx]
    src_page = doc[src_doc_idx]
    nodes.append(node)
nodes

[TextNode(id_='e8017f28-b912-4a46-a231-2a1017ca87ff', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, text='0 \n \n \n 1 \n  \n \nThe Word: Student Handbook \n2023-2024 \n2 \n \n \nWelcome to The Word 2023-2024 \n \nThe Word student handbook contains information and resources to help you create your \nCarnegie Mellon experience and embrace your role as a valued member of our university. At Carnegie Mellon, our ambition is that all students will reach their highest potential in the \nareas of intellectual and artistic pursuits, personal well-being, professional development, \nleadership, and contribution to the larger community. Community membership affords many privileges and likewise responsibilities as we all uphold \nthe standards of our university. To ensure you are knowledgeable of the university’s \nexpectations and the process that will be followed if standards are not met, this handbook \narticulates the rights and 

In [13]:
len(nodes)

205

In [18]:
# Name our Pinecone Index:
index_name = "hw02"

# If a Pinecone index of the same name already exists, delete it:
if index_name in pc.list_indexes().names():
    pc.delete_index(index_name)

In [19]:
use_serverless = os.environ.get("USE_SERVERLESS", "False").lower() == "true"

if use_serverless:
    spec = pinecone.ServerlessSpec(cloud='aws', region='us-west-2')
else:
    spec = pinecone.PodSpec(environment=environment)

# Name our Pinecone Index:
index_name = "hw02"

# If a Pinecone index of the same name already exists, delete it:
if index_name in pc.list_indexes().names():
    pc.delete_index(index_name)

In [20]:
# Name our Pinecone Index:
index_name = "hw02"

# define similarity and additional parameters for the vector store index:

dimensions = 1536 #768              # the dimensions of the index need to align with the LLM we are using for the RAG system. For example, if using openAI then dimenion = 1536. If using Llama2, then dimension = 384.

# "dotproduct" is one similarity metric we can for the vector store index. We can use different distance metrics to measure the similarity between vector embeddings and user queries. This is where we define what similarity metric we are going to use for the vector store.
# "cosine" is another similarity metric we can use for the vector store index.
# "euclidean" is another similarity metric we can use for the vector store index.

pc.create_index(
    name=index_name, 
    dimension=dimensions, 
    metric="cosine",          # we can use different distance metrics to measure the similarity between vector embeddings and user queries. this is where we define what similarity metric we are going to use for the vector store.
    spec=spec
)

# wait for index to be ready before connecting
while not pc.describe_index(index_name).status['ready']:
    time.sleep(1)

for index in pc.list_indexes():
    print(index['name'])


pc.describe_index("hw02")


pc_index = pc.Index(index_name)  # create an index to use in the vector store


vector_store = PineconeVectorStore(pinecone_index=pc_index)    # this function creates a vector store where we will add and store embeddings

hw02


In [21]:
pc_index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [40]:

llm = OpenAI(model="gpt-3.5-turbo", api_key=openai)


extractors = [
    TitleExtractor(nodes=5, llm=llm),
    QuestionsAnsweredExtractor(questions=3, llm=llm),
]

pipeline = IngestionPipeline(
    transformations=extractors,
)
nodes = await pipeline.arun(nodes=nodes, in_place=False)


0it [00:00, ?it/s]


In [22]:
model_ada="text-embedding-ada-002"
small_txt_embedmodel_="text-embedding-3-small"

In [23]:
embed_model = OpenAIEmbedding(model="text-embedding-3-small", openai_api_key=openai)

for node in nodes:
    node_embedding = embed_model.get_text_embedding(
        node.get_content(metadata_mode="all")
    )
    node.embedding = node_embedding

vector_store.add(nodes)

Upserted vectors:   0%|          | 0/205 [00:00<?, ?it/s]

['f65f76fc-aba1-4e25-b838-faaa4238cfff',
 '98dba768-f15d-49b3-ac93-0741739d2c03',
 '2cd1927b-b80c-4c1d-9510-238cfbfadf03',
 '38a9ac6b-fda5-4105-8f53-f6b2c2417075',
 '1a2c9ba8-0d60-4b04-b5e4-cc8748500bbd',
 '36f290aa-4b8e-415c-bd71-66e0a30491ed',
 '9f1ac3da-8c74-486e-a6bc-ea5a9ffbf0d0',
 '00dc921a-392c-44a3-a014-6e2f0359a617',
 'b24a55b8-4171-4f39-9f80-6e31c716e299',
 'b363d131-6f35-4be3-a6a1-3e19411ab535',
 'ce758f13-225b-4244-8bb8-1af4d74be791',
 '20b26b99-93ac-4bb9-9ebc-65c4b0281e73',
 '00545ff1-c015-4d5b-be74-a591dcd834dc',
 '26db22dc-efad-44d1-b1df-13ad932f3ca0',
 '37b43586-46a5-4b54-ae2b-d3e7336398ff',
 '35784cc1-de49-49db-a5db-c808e6354f7f',
 '69ad1524-003d-4b95-aa6d-fe2437765c6c',
 'a33e940a-e700-48dc-ae5a-1dc20e2d4288',
 '1b0c92c5-f3dc-463e-ba8e-453145de9e51',
 'fea940ca-8c67-4a78-9571-a62032f80f31',
 '8af4c255-a899-49dc-b675-19f769c93a7b',
 '2ea60d58-a04d-4a13-955a-5de625e6a594',
 'fedb2d60-d6dd-42b2-908f-9de621cfbf03',
 '75c4f57a-93df-4e84-9fc7-36ec23d5b933',
 '2f948ebe-42b6-

In [ ]:
vector_store.add(nodes)

Upserted vectors: 100%|██████████| 205/205 [00:02<00:00, 97.46it/s] 


['89844d20-92f6-41ca-9c5a-7eb9a2c092f5',
 '4ddf31fa-3c77-4516-9ab9-0584419aac2d',
 '78a0970a-575b-45e9-a8b7-54281faacbd1',
 '77f6124f-8024-4dd6-8ffa-0ecbf55a08a7',
 '077b9a76-58ee-4d49-a9bb-0e49b4b97ed6',
 'aaeaade3-65df-4201-9d00-273c448850ee',
 '170d763d-8df8-4482-8cb0-d2b2e9b91ddd',
 '175b604f-95ea-43ce-a3ef-e1f6b201207e',
 '3cfc6957-e8dc-4529-8dd0-d2a55f1ceb4f',
 '7e071f96-2d1d-48bf-892d-d8cb2ed4da01',
 '84215ec7-1ed7-47bc-b9a9-75399fbcc714',
 '2fea4e63-1c39-49af-90c1-b38d76c07158',
 'a658a551-ab7e-4419-8741-1b54bf4a7195',
 '62259983-aa01-4076-b9cb-cbe8745ddc65',
 'c0d1a2b9-b6a5-4e95-aac8-ac97148c3d69',
 '728cc00d-fcaa-4427-8f22-183cfd72ac02',
 '49eb6481-62f5-4c51-a00b-6f103404fddd',
 'be1f83d0-62fd-4833-9282-a4a4aaf26485',
 '4cad0d18-3684-45f9-b5cb-d6d95cd8b221',
 'fa268559-ed24-4c09-bbe2-507355b897ca',
 '70b03b73-6d5e-4ea6-a509-857c22be0ae7',
 'bc408170-888d-400b-a43b-ae6e1c503016',
 '8807eb75-9aef-422c-b65a-0658ae9dbdf7',
 'e8a5c16a-8828-4314-a972-5897ac4fb659',
 '069f42a2-1658-

In [25]:

pc_index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.00205,
 'namespaces': {'': {'vector_count': 205}},
 'total_vector_count': 205}

In [14]:
print(nodes[0].metadata)

{}


In [ ]:
query = (
    "What is the policy violation definition for cheating?"
)

embed_model_ada = "text-embedding-ada-002"
embed_model_3_small = "text-embedding-3-small"

res = client.embeddings.create(
    input=[query],
    model= embed_model_ada 
)

# retrieve from Pinecone
xq = res.data[0].embedding #res['data'][0]['embedding']

k=[5,10, 50, 75, 100, 500]
# get relevant contexts (including the questions)
with open('results.txt', 'w') as file:
    for k_value in k: 
        file.write(f'\n K = {k_value}\n--------------\n')
        print('\n K =',k_value,'\n--------------\n')
        reshw = pc_index.query(vector=xq, top_k=k_value, include_metadata=False)
        for index, result in enumerate(reshw.matches):
            for node in nodes:
                if node.id_ == result.id:
                    print('Result',index,'(score=',result.score,') ',node,'\n----------')
                    file.write(f'Result {index} (score={result.score}) {node}\n----------\n')



 K = 5 
--------------

Result 0 (score= 0.0945086554 )  Node ID: 3cfc6957-e8dc-4529-8dd0-d2a55f1ceb4f
Text: 8       Use of an alternate, stand-in or proxy during an
examination. 3. Copying from the examination or work of another person
or source. 4. Submission or use of falsified data. 5. Using false
statements to obtain additional time or other accommodation. 18
6. 
----------
Result 1 (score= 0.0910882205 )  Node ID: 717c4ef1-51af-4a75-885a-5451a4799d55
Text: 181       The  University Police are responsible for keeping the
tunnels locked and apprehending anyone  who trespasses in them.
Student Accounts Receivable Collection Policy and Procedures  Please
refer to the current Student Financial Obligation Statement. That
statement is  provided to all students through the Student Information
Online (SIO). 
----------
Result 2 (score= 0.0910409093 )  Node ID: a31bda62-5c54-4044-a02a-b1084b1aed54
Text: 115       Participate in periodic safety inspections of the work
area. Environmental H

In [ ]:
with open('results.txt', 'w') as file:
    # Get relevant contexts (including the questions)
    for k_value in [5,10]:
        file.write(f'\n K = {k_value}\n--------------\n')
        reshw = pc_index.query(vector=xq, top_k=k_value, include_metadata=False)
        for index, result in enumerate(reshw.matches):
            for node in nodes:
                if node.id_ == result.id:
                    file.write(f'Result {index}\n')
                    file.write(f'Score: {result.score}\n')
                    file.write(f'Node: {node.text}\n')
                    file.write('----------\n')

print("Results have been written to results.txt file.")


Results have been written to results.txt file.


### **Homework Questions:**

**B.I.** Explain your rationale for selecting the query you choose in B.1. Why did you choose this query vs. the other 4 queries? 

**B.II.** Copy and paste the responses to the 6 queries you submitted to the vector store, as described in B.1 above.

	Response 1 (to Query A): 


	Response 2 (to Query B): 


	Response 3 (to Query C): 


	Response 4 (to Query D): 


	Response 5 (to Query E): 
    

    Response 5 (to Query F): 

**B.III.** Copy and paste the responses to the 6 queries you submitted to the vector store, as described in B.2 above. 

	Response 1 (to Query A): 


	Response 2 (to Query B): 


	Response 3 (to Query C): 


	Response 4 (to Query D): 


	Response 5 (to Query E): 
    

    Response 5 (to Query F): 

**B.IV.** In observing the responses from the vector store to the 6 queries created in B.1., which ‘k’ parameter do you think retrieved the highest quality / most accurate result? Why do you think this parameter was the best to use with the query?

**B.V.** In observing the responses from the vector store to the 6 queries created in B.2., which ‘k’ parameter do you think retrieved the highest quality / most accurate result? Why do you think this parameter was the best to use with the query?

# **BONUS TASKS / QUESTIONS: Define function to call LLM API**

In [15]:
#load the pinecone Index. It should have the last vectors embeddings. If you need to change the textsplit method go back to previous steps
index_name = "hw02"
pc_index = pc.Index(index_name)  # load index to use in the vector store
pc.describe_index("hw02")

{'dimension': 1536,
 'host': 'hw02-cmx69u7.svc.gcp-starter.pinecone.io',
 'metric': 'cosine',
 'name': 'hw02',
 'spec': {'pod': {'environment': 'gcp-starter',
                  'pod_type': 'starter',
                  'pods': 1,
                  'replicas': 1,
                  'shards': 1}},
 'status': {'ready': True, 'state': 'Ready'}}

In [16]:
def get_top_messages(q, k):
    from openai import OpenAI
    client = OpenAI()
    embed_model_ada = "text-embedding-ada-002"
    res = client.embeddings.create(
        input=[q],
        model= embed_model_ada 
    )
    # retrieve from Pinecone
    xq = res.data[0].embedding
    # get relevant contexts
    pc_results = pc_index.query(vector=xq, top_k=k, include_metadata=False)
    results=[]
    for index, result in enumerate(pc_results.matches):
        for node in nodes:
            if node.id_ == result.id:
                results.append(node.text)
                #return node.text
    return ", ".join(results) 


In [17]:
def rag_llm(model, q, k):
    import openai
    f=get_top_messages(q, k)

    client = openai.OpenAI(
            base_url = "https://api.endpoints.anyscale.com/v1",
            api_key=access_endpoint_api_key
            )

    # Define the messages
    messages = [
        {"role": "system", "content": f},
        {"role": "user", "content": q}]

    # Call the completions endpoint (e.g. the LLM API)
    response = client.chat.completions.create(
        model= model, 
        messages=messages,
    )
    responseContent = response.choices[0].message.content
    responseContentStr = str(responseContent)
    return responseContentStr, responseContent, f #, print(f"MODEL: {model}--RESUME SUMMARY: \n\n{responseContent}") 



### **Call LLM API**

In [18]:
model_01 = "mistralai/Mixtral-8x7B-Instruct-v0.1"
model_02 = "google/gemma-7b-it"
model_03="meta-llama/Llama-2-7b-chat-hf"

In [19]:
access_endpoint_api_key

'esecret_61tzd29pm45ysdw5btxiqbklyd'

In [58]:
test=get_top_messages("What is the policy statement for the academic integrity policy?", 10)
test

"51 \n \n \nstudy (five for architecture) based upon the maintenance of a specific cumulative quality \npoint average. The academic scholarship renewal criteria are included in the scholarship \nnotification letter which is mailed to the student prior to the May 1 matriculation deadline. \nEach scholarship recipient's cumulative quality point average is reviewed at the end of \neach academic year. If the student achieves the scholarship renewal criteria, then the \nscholarship is automatically renewed for the next academic year. \nIf the student does not meet the cumulative quality point average requirement for \nrenewal, then s/he is given the opportunity to appeal. A merit scholarship appeal form \nand instructions are automatically sent to the student at the end of each academic year. \nThe student's completed appeal form is reviewed by members of the Enrollment Services \nstaff. Input from the Associate Dean of the student's college is also considered. The \nstudent is notified, in

In [59]:
# MistralAI Model:
textA, __, original_messageA =rag_llm(model=model_01, q="What is the policy violation definition for cheating?", k=10)

textA

' The policy violation definition for cheating is not provided in the text you have given. However, plagiarism is defined as the use of work or concepts contributed by other individuals without proper attribution or citation. Unique ideas or materials taken from another source for either written or oral use must be fully acknowledged in academic work to be graded. Examples of sources expected to be referenced include but are not limited to: text, either written or spoken, quoted directly or paraphrased; graphic elements; passages of music, existing either as sound or as notation; mathematical proofs; scientific data; concepts or material derived from the work, published or unpublished, of another person. Unauthorized assistance is also considered a violation, and it refers to the use of sources of support that have not been specifically authorized in this policy statement or by the course instructor(s) in the completion of academic work to be graded. Examples of unauthorized assistance

In [69]:
# Google Gemma Model:
textB, __, original_messageB=rag_llm(model=model_02, q="What is the policy violation definition for cheating?", k=10)
textB

'The text does not define the policy violation definition for cheating, therefore I cannot answer this question.'

In [68]:
# Llama2 model:
textC, __, original_messageC=rag_llm(model=model_03, q="What is the policy violation definition for cheating?", k=7)
textC

'  The policy violation definition for cheating at Carnegie Mellon University is as follows:\n\n"Cheating: Unethical behavior, including but not limited to:\n\n• Plagiarism: Using work or concepts contributed by another individual without proper attribution or citation, including copying or paraphrasing work from the internet or other sources without proper citation.\n• Fabrication: Making up data, results, or sources without proper justification or documentation.\n• Misconduct: Violating established procedures for completing academic work, including but not limited to, submission of work completed by someone else, collusion, or unauthorized assistance.\n• Bribery: Offering, giving, receiving or soliciting unauthorized aid in connection with any academic exercise or assessment.\n• Falsification: Misrepresenting information, including but not limited to, falsifying data, sources, or qualifications, or submitting false reports or applications.\n• Assisting others: Intentionally helping o

In [62]:
original_messageA

"259 \n \n \nSteam Tunnels \nBecause of the danger to all who enter them, the steam tunnels are locked and anyone \nfound in the tunnels will be subject to serious disciplinary action and/or criminal action. The \nUniversity Police are responsible for keeping the tunnels locked and apprehending anyone \nwho trespasses in them. \nStudent Accounts Receivable Collection Policy and Procedures \nPlease refer to the current Student Financial Obligation Statement. That statement is \nprovided to all students through the Student Information Online (SIO). Questions about this \nstatement may be directed to The HUB. \nStudent Damage to Carnegie Mellon Property Policy \nStudents will be charged with the cost of restoring to its proper condition any Carnegie \nMellon property that, through their negligence or misuse, has been damaged. \nResponsible parties will be subject to disciplinary action if said damages are found to have \nbeen intentional or caused as a result of improper behavior. All suc

#### Evaluating LLM Responses

In [63]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

def compare_text_similarity(text_a, text_b, text_c):
    """
    Compares the similarity between three texts using TF-IDF vectors and cosine similarity.
    
    Parameters:
    - text_a (str): Text A
    - text_b (str): Text B
    - text_c (str): Text C
    
    Returns:
    - A dictionary with similarity scores between Text A & Text B, A & C, and B & C.
    """
    # Initialize the vectorizer and transform texts into TF-IDF vectors
    vectorizer = TfidfVectorizer()
    tfidf_matrix = vectorizer.fit_transform([text_a, text_b, text_c])
    
    # Calculate cosine similarity
    similarity_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)
    
    # Similarity between Text A and B, A and C, and then B and C
    similarity_scores = {
        "A_B": similarity_matrix[0, 1],
        "A_C": similarity_matrix[0, 2],
        "B_C": similarity_matrix[1, 2]
    }

    return similarity_scores

def compare_text_similarity_response2context(om, model_response):
    """
    Compares the similarity between three texts using TF-IDF vectors and cosine similarity.
    
    Parameters:
    - text_a (str): Text A
    - text_b (str): Text B
    - text_c (str): Text C
    
    Returns:
    - A dictionary with similarity scores between Text A & Text B, A & C, and B & C.
    """
    # Initialize the vectorizer and transform texts into TF-IDF vectors
    vectorizer = TfidfVectorizer()
    tfidf_matrix = vectorizer.fit_transform([om, model_response])
    
    # Calculate cosine similarity
    similarity_matrix = cosine_similarity(tfidf_matrix, tfidf_matrix)
    
    # Similarity between Text A and B, A and C, and then B and C
    similarity_scores = {
        "A_B": similarity_matrix[0, 1],
        #"A_C": similarity_matrix[0, 2],
        #"B_C": similarity_matrix[1, 2]
    }

    return similarity_scores

In [64]:
similarities = compare_text_similarity(text_a=textA, text_b=textB, text_c=textC)
#similarities
print("LLM Response Similarity Scores:")
for pair, score in similarities.items():
    print(f"{pair}: {score:.4f}")

LLM Response Similarity Scores:
A_B: 0.1966
A_C: 0.5983
B_C: 0.1096


In [65]:
similaritiesOM = compare_text_similarity(text_a=original_messageA, text_b=original_messageB, text_c=original_messageC)
#similaritiesOM
print("System Prompt/Context Similarity 2  System Prompt/Context Similarity Scores:")
for pair, score in similaritiesOM.items():
    print(f"{pair}: {score:.4f}")

System Prompt/Context Similarity 2  System Prompt/Context Similarity Scores:
A_B: 1.0000
A_C: 0.9842
B_C: 0.9842


In [66]:
similaritiesOM_LLM_A =compare_text_similarity_response2context(om=original_messageA, model_response=textA)
similaritiesOM_LLM_B =compare_text_similarity_response2context(om=original_messageB, model_response=textB)
similaritiesOM_LLM_C =compare_text_similarity_response2context(om=original_messageC, model_response=textC)

print("System Prompt/Context to LLM Response \n Similarity Scores \n Model 1:")
for pair, score in similaritiesOM_LLM_A.items():
    print(f"{pair}: {score:.4f}")
print("\n")
print("System Prompt/Context to LLM Response\n Similarity Scores \n Model 2:")
for pair, score in similaritiesOM_LLM_B.items():
    print(f"{pair}: {score:.4f}")
print("\n")
print("System Prompt/Context to LLM Response\n Similarity Scores \n Model 3:")
for pair, score in similaritiesOM_LLM_C.items():
    print(f"{pair}: {score:.4f}")

System Prompt/Context to LLM Response 
 Similarity Scores 
 Model 1:
A_B: 0.7315


System Prompt/Context to LLM Response
 Similarity Scores 
 Model 2:
A_B: 0.2567


System Prompt/Context to LLM Response
 Similarity Scores 
 Model 3:
A_B: 0.5361
